In [1]:
import pandas as pd
from PyPDF2 import PdfReader
import fitz  # PyMuPDF
import pdfplumber
from pdfminer.high_level import extract_pages
from PyPDF4 import PdfFileReader
import time
import os


def count_pages_all_methods(pdf_path):
    results = []

    t0 = time.time()
    # Метод 1: PyPDF2
    try:
        reader = PdfReader(pdf_path)
        l = len(reader.pages)
    except Exception as e:
        print(f"Ошибка в PyPDF2 ({pdf_path}): {e}")
        l = None

    t1 = time.time()
    results.append((l, f'{t1 - t0:.2f}'))

    # Метод 2: PyMuPDF (fitz)
    try:
        doc = fitz.open(pdf_path)
        l = doc.page_count
    except Exception as e:
        print(f"Ошибка в PyMuPDF ({pdf_path}): {e}")
        l = None

    t2 = time.time()
    results.append((l, f'{t2 - t1:.2f}'))
    # Метод 3: pdfplumber
    try:
        with pdfplumber.open(pdf_path) as pdf:
            l = len(pdf.pages)
    except Exception as e:
        print(f"Ошибка в pdfplumber ({pdf_path}): {e}")
        l = None

    t3 = time.time()
    results.append((l, f'{t3 - t2:.2f}'))
    # Метод 4: PDFMiner
    try:
        print(1/0)
        num_pages = sum(1 for _ in extract_pages(pdf_path))
        l = num_pages
    except Exception as e:
        print(f"Ошибка в PDFMiner ({pdf_path}): {e}")
        l = None

    t4 = time.time()
    results.append((l, f'{t4 - t3:.2f}'))
    # Метод 5: PyPDF4
    try:
        with open(pdf_path, 'rb') as f:
            reader = PdfFileReader(f)
            l = reader.numPages
    except Exception as e:
        print(f"Ошибка в PyPDF4 ({pdf_path}): {e}")
        l = None
    t5 = time.time()
    results.append((l, f'{t5 - t4:.2f}'))
    return tuple(results)


# Список PDF файлов

directory = os.getcwd()  # Замените на путь к вашей директории
directory = r'c:\Users\ksree\Documents\GitHub\Parsing'
pdf_files = []
Number_of_pages = []

# Обход директории и вложенных папок
for root, dirs, files in os.walk(directory):
    for file in files:
        if file.endswith(".pdf"):
            # Добавляем полный путь к файлу в список
#            pdf_files.append(os.path.join(root, file))
            pdf_files.append(file)




# Создание общего списка
results_list = []
for pdf_file in pdf_files:
    page_counts = count_pages_all_methods(pdf_file)
    results_list.append((pdf_file, *page_counts))

# Создание DataFrame
columns = ["File Name", "PyPDF2", "PyMuPDF", "pdfplumber", "PDFMiner", "PyPDF4"]
df = pd.DataFrame(results_list, columns=columns)

# Сохранение DataFrame в CSV (если нужно)
try:
    df.to_csv("pdf_page_counts.csv", index=False, encoding = 'utf-8-sig')
except:
    df.to_csv("pdf_page_counts1.csv", index=False, encoding = 'utf-8-sig')

# Вывод DataFrame
print(df)


Empty DataFrame
Columns: [File Name, PyPDF2, PyMuPDF, pdfplumber, PDFMiner, PyPDF4]
Index: []


In [3]:
import fitz
print(fitz.__doc__)


PyMuPDF 1.25.0: Python bindings for the MuPDF 1.25.1 library (rebased implementation).
Python 3.12 running on win32 (64-bit).



In [4]:
import fitz  # PyMuPDF

def extract_pages(input_pdf, output_pdf, start_page, end_page):
    """
    Извлекает страницы из PDF в заданном диапазоне и сохраняет их в новый PDF.

    :param input_pdf: Путь к исходному PDF-файлу.
    :param output_pdf: Путь для сохранения нового PDF-файла.
    :param start_page: Номер начальной страницы (считается с 1).
    :param end_page: Номер конечной страницы (включительно, с 1).
    """
    try:
        # Открываем исходный PDF-файл
        doc = fitz.open(input_pdf)

        # Создаем новый PDF-документ
        new_doc = fitz.open()

        # Добавляем страницы из указанного диапазона
        for page_num in range(start_page - 1, end_page):
            new_doc.insert_pdf(doc, from_page=page_num, to_page=page_num)

        # Сохраняем новый PDF
        new_doc.save(output_pdf)
        new_doc.close()
        doc.close()

        print(f"Страницы с {start_page} по {end_page} сохранены в {output_pdf}.")
    except Exception as e:
        print(f"Ошибка: {e}")

# Пример использования
input_pdf_path = "ASME Sec II-D-Metric.pdf"  # Укажите путь к исходному PDF-файлу
#input_pdf_path = "extracted_pages.pdf"
output_pdf_path = "extracted_pages450.pdf"  # Укажите путь для нового файла
start = 450  # Номер начальной страницы
end = 460  # Номер конечной страницы

extract_pages(input_pdf_path, output_pdf_path, start, end)


Страницы с 450 по 460 сохранены в extracted_pages450.pdf.


In [8]:
import fitz  # PyMuPDF
import os

def extract_text_from_pdf(pdf_path, output_txt_path=None):
    """
    Извлекает текст из PDF-документа и (опционально) сохраняет его в текстовый файл.

    :param pdf_path: Путь к PDF-файлу.
    :param output_txt_path: Путь для сохранения извлечённого текста (опционально).
    :return: Извлечённый текст в виде строки.
    """
    try:
        # Открываем PDF-документ
        doc = fitz.open(pdf_path)
        text = ""

        # Проходим по всем страницам документа
        for page_num in range(len(doc)):
            page = doc[page_num]
            text += page.get_text()  # Извлекаем текст из текущей страницы
            text += "\n"  # Добавляем перевод строки между страницами

        doc.close()

        # Сохраняем текст в файл, если указан путь
        if output_txt_path:
            with open(output_txt_path, "w", encoding="utf-8") as f:
                f.write(text)

        return text

    except Exception as e:
        print(f"Ошибка: {e}")
        return None


def find_pdf_files(directory):
    pdf_files = []
    for root, dirs, files in os.walk(directory):
        for file in files:
            if file.lower().endswith('.pdf'):
                pdf_files.append(os.path.join(root, file))
    return pdf_files



# Пример использования
pdf_file = "extracted_pages450.pdf"  # Укажите путь к PDF-файлу
directory = r'c:\Users\ksree\Documents\GitHub\Parsing'
pdf_list = find_pdf_files(directory)

l = len(pdf_list)
for i in range(1):
    print('i = ', i)
    print()
    pdf_file = pdf_list[i]
    print(pdf_file)
    output_text_file = "extracted_text.txt"  # Укажите путь для сохранения текста (опционально)

    # Извлекаем текст
    extracted_text = extract_text_from_pdf(pdf_file, output_text_file)

    # Печать извлечённого текста в консоль
    if extracted_text:
        print("Извлечённый текст:")
        print(extracted_text)


i =  0

c:\Users\ksree\Documents\GitHub\Parsing\ASME Sec II-D-Metric.pdf
Извлечённый текст:
SECTION II
MATERIALS
Part D
Proper ties (Metric)
ASME BPVC.II.D.M-2023
2023
ASME Boiler and
Pressure Vessel Code
An International Code

Markings such as “ASME,” “ASME Standard,” or any other marking including “ASME,” ASME logos, 
or the ASME Single CerƟﬁcaƟon Mark shall not be used on any item that is not constructed in 
accordance with all of the applicable requirements of the Code or Standard. Use of the ASME 
Single CerƟﬁcaƟon Mark requires formal ASME cerƟﬁcaƟon; if no cerƟﬁcaƟon program is 
available, such ASME markings may not be used. (For CerƟﬁcaƟon and AccreditaƟon Programs, 
see hƩps://www.asme.org/cerƟﬁcaƟon-accreditaƟon.)
Items produced by parƟes not formally possessing an ASME CerƟﬁcate may not be described, 
either explicitly or implicitly, as ASME cerƟﬁed or approved in any code forms or other document.

II
MATERIALS
Part D
Properties (Metric)
ASME Boiler and Pressure Vessel Commi